In [1]:
import qorelib as q
from scipy.linalg import expm
import numpy as np
from numpy import ndarray, matrix, complexfloating, array
import plotly.graph_objects as go
import random
from tqdm import tqdm
from scipy.optimize import leastsq


In [2]:
OmegaQ1: float = 2 * np.pi * 5000
OmegaQ2: float = 2 * np.pi * 9600
OmegaD: float = 2 * np.pi * 5000 + 2 * np.pi * 1  # 这个频率是角频率
a: complexfloating = 1
b: complexfloating = 0
c: complexfloating = 0
A: float = 30 * 2 * np.pi * 1
PhiD: float = np.pi / 2 * 0


In [3]:
initialState: matrix = matrix([[a], [b], [c]])


In [4]:
def HamiltonianWithDrive3X3X(omegaQ1: float, omegaQ2: float, omegaD: float, phiD: float, A: float):
    return matrix([[0, 0.5 * A * np.exp(1j * phiD), 0],
                   [0.5 * A * np.exp(-1j * phiD), omegaQ1 - omegaD,
                    (np.sqrt(2) / 2) * A * np.exp(1j * phiD)],
                   [0, (np.sqrt(2) / 2) * A * np.exp(-1j * phiD),  omegaQ2 - 2 * omegaD]])


def HamiltonianWithoutDrive3X3(omegaQ1: float, omegaQ2: float, omegaD: float):
    return matrix([[0, 0, 0], [0, omegaQ1 - omegaD, 0], [0, 0, omegaQ2 - 2 * omegaD]])


In [5]:
data: list = []
precision: int = 10
for omegaD in tqdm(range(int(4750 * 2 * np.pi * precision), int(5150 * 2 * np.pi * precision)), desc="Computing ... ", colour='green'):
    momegaD = omegaD / precision
    currentState = q.ComputeState(initialState, 10, HamiltonianWithDrive3X3X(
        OmegaQ1, OmegaQ2, momegaD, PhiD, A))
    probability0 = q.ComputeStateProbability(currentState, 0)
    data.append([momegaD / (2 * np.pi), probability0])
ndData = np.array(data)


Computing ... : 100%|██████████| 25133/25133 [00:02<00:00, 11574.88it/s]


In [6]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=ndData[:, 0], y=ndData[:, 1], name="state 0 probability", mode='markers')
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        'text': "S21双信号谱",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    xaxis_title="ωd(GHz)",
    yaxis_title="0态概率",
    font=dict(
        color="black"
    ),
    width=800,
)
fig.show()


# Time Rabi

In [7]:
# Ωd = Ωq2
OmegaD_M1 = OmegaQ2
data: ndarray = np.array([[0, 0]])
stateData: ndarray = np.array([[0, 0, 0]])
τ: float = 0.3
precision: int = 1000
for t in tqdm(range(0, int(τ * precision)), desc="Computing ... ", colour="#12c462"):
    td = t / precision
    currentState: matrix = q.ComputeState(
        initialState, td, HamiltonianWithDrive3X3X(OmegaQ1, OmegaQ2, OmegaD_M1, PhiD, A))
    if t == 0:
        stateData[0] = np.array(currentState.T)
    else:
        stateData = np.r_[stateData, currentState.T]
    if t == 0:
        data[0] = np.array([td, q.ComputeStateProbability(currentState, 0)])
    else:
        data = np.r_[data, np.array(
            [[td, q.ComputeStateProbability(currentState, 0)]])]


Computing ... :   0%|          | 0/300 [00:00<?, ?it/s]C:\Users\seanw\AppData\Local\Temp\ipykernel_7428\3120533704.py:12: ComplexWarning:

Casting complex values to real discards the imaginary part

Computing ... : 100%|██████████| 300/300 [00:00<00:00, 8213.93it/s]


In [8]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=data[:, 0], y=data[:, 1], name="state 0 probability", mode='markers')
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        'text': "Rabi振荡：ωd=ωq2",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    xaxis_title="t(μs)",
    yaxis_title="0态概率",
    font=dict(
        color="black"
    ),
    width=800,
)
fig.show()


In [9]:
coo = []
for states in stateData:
    a: complexfloating = states[0, 0]
    b: complexfloating = states[0, 1]
    alpha: float = np.angle(a)
    beta: float = np.angle(b)
    phi: float = beta - alpha
    theta: float = 2 * np.arccos(np.abs(a))
    x: float = np.sin(theta) * np.cos(phi)
    y: float = np.sin(theta) * np.sin(phi)
    z: float = np.cos(theta)
    coo.append([x, y, z])
ndCoo: ndarray = np.array(coo)

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(0, np.pi / 2, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z,
                                opacity=0.3,
                                color='#FFD88F'
                                )])

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(np.pi / 2, np.pi, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig.add_trace(
    go.Mesh3d(x=x, y=y, z=z,
              opacity=0.3,
              color='#FFD88F',
              )
)


fig.add_trace(
    go.Scatter3d(
        x=ndCoo[:, 0],
        y=ndCoo[:, 1],
        z=ndCoo[:, 2],
        mode='markers',
        marker=dict(color='red', size=4,)
    )
)

fig.update_traces(
    colorbar=dict(
        thickness=0
    ),
    selector=dict(
        type='surface'
    )

)

fig.update_layout(
    title={
        'text': "量子比特态在布洛赫球上运动轨迹：ωd=ωq2",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    font=dict(
        color="black"
    ),
    scene=dict(
        xaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(200, 200, 230)",
        ),
        yaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 200, 230)",
        ),
        zaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 230, 200)",
        ),
    ),
    scene_aspectmode='cube',
    width=800,
    height=800,
)

fig.show()


In [25]:
# Ωd = Ωq2 / 2
OmegaD_M1 = OmegaQ2 / 2
data: ndarray = np.array([[0, 0]])
stateData: ndarray = np.array([[0, 0, 0]])
# τ: float = 0.3
τ: float = (2 * np.pi) / ((A**2 * np.sqrt(2)) / (2 * (OmegaQ1 - 0.5 * OmegaQ2)))
precision: int = 10000
for t in tqdm(range(0, int(τ * precision)), desc="Computing ... ", colour="#12c462"):
    td = t / precision
    currentState: matrix = q.ComputeState(
        initialState, td, HamiltonianWithDrive3X3X(OmegaQ1, OmegaQ2, OmegaD_M1, PhiD, A))
    if t == 0:
        stateData[0] = np.array(currentState.T)
    else:
        stateData = np.r_[stateData, currentState.T]
    if t == 0:
        data[0] = np.array([td, q.ComputeStateProbability(currentState, 2)])
    else:
        data = np.r_[data, np.array(
            [[td, q.ComputeStateProbability(currentState, 2)]])]


Computing ... :   0%|          | 0/3142 [00:00<?, ?it/s]C:\Users\seanw\AppData\Local\Temp\ipykernel_7428\1963903874.py:13: ComplexWarning:

Casting complex values to real discards the imaginary part

Computing ... : 100%|██████████| 3142/3142 [00:00<00:00, 11652.48it/s]


In [26]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=data[:, 0], y=data[:, 1], name="state 0 probability", mode='markers')
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        'text': "Rabi振荡：ωd=ωq2 / 2",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    xaxis_title="t(μs)",
    yaxis_title="0态概率",
    font=dict(
        color="black"
    ),
    width=800,
)
fig.show()


In [12]:
# Ωd = Ωq1 / 2
OmegaD_M1 = OmegaQ1 / 2
data: ndarray = np.array([[0, 0]])
stateData: ndarray = np.array([[0, 0, 0]])
τ: float = 0.3
precision: int = 10000
for t in tqdm(range(0, int(τ * precision)), desc="Computing ... ", colour="#12c462"):
    td = t / precision
    currentState: matrix = q.ComputeState(
        initialState, td, HamiltonianWithDrive3X3X(OmegaQ1, OmegaQ2, OmegaD_M1, PhiD, A))
    if t == 0:
        stateData[0] = np.array(currentState.T)
    else:
        stateData = np.r_[stateData, currentState.T]
    if t == 0:
        data[0] = np.array([td, q.ComputeStateProbability(currentState, 0)])
    else:
        data = np.r_[data, np.array(
            [[td, q.ComputeStateProbability(currentState, 0)]])]


Computing ... :   0%|          | 0/3000 [00:00<?, ?it/s]C:\Users\seanw\AppData\Local\Temp\ipykernel_7428\1929882442.py:12: ComplexWarning:

Casting complex values to real discards the imaginary part

Computing ... : 100%|██████████| 3000/3000 [00:00<00:00, 9811.91it/s] 


In [13]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=data[:, 0], y=data[:, 1], name="state 0 probability", mode='markers')
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        'text': "Rabi振荡：ωd=ωq1 / 2",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    xaxis_title="t(μs)",
    yaxis_title="0态概率",
    font=dict(
        color="black"
    ),
    width=800,
)
fig.show()


In [14]:
coo = []
for states in stateData:
    a: complexfloating = states[0, 0]
    b: complexfloating = states[0, 1]
    alpha: float = np.angle(a)
    beta: float = np.angle(b)
    phi: float = beta - alpha
    theta: float = 2 * np.arccos(np.abs(a))
    x: float = np.sin(theta) * np.cos(phi)
    y: float = np.sin(theta) * np.sin(phi)
    z: float = np.cos(theta)
    coo.append([x, y, z])
ndCoo: ndarray = np.array(coo)

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(0, np.pi / 2, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z,
                                opacity=0.3,
                                color='#FFD88F'
                                )])

Phi = np.linspace(0, 2 * np.pi, 100)
Theta = np.linspace(np.pi / 2, np.pi, 100)

x, y, z = [], [], []
for theta in Theta:
    for phi in Phi:
        x.append(np.sin(theta) * np.cos(phi))
        y.append(np.sin(theta) * np.sin(phi))
        z.append(np.cos(theta))

fig.add_trace(
    go.Mesh3d(x=x, y=y, z=z,
              opacity=0.3,
              color='#FFD88F',
              )
)


fig.add_trace(
    go.Scatter3d(
        x=ndCoo[:, 0],
        y=ndCoo[:, 1],
        z=ndCoo[:, 2],
        mode='markers',
        marker=dict(color='red', size=4,)
    )
)

fig.update_traces(
    colorbar=dict(
        thickness=0
    ),
    selector=dict(
        type='surface'
    )

)

fig.update_layout(
    title={
        'text': "量子比特态在布洛赫球上运动轨迹：ωd=ωq1 / 2",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    font=dict(
        color="black"
    ),
    scene=dict(
        xaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(200, 200, 230)",
        ),
        yaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 200, 230)",
        ),
        zaxis=dict(
            range=[-1.3, 1.3],
            dtick=0.5,
            showbackground=True,
            backgroundcolor="rgb(230, 230, 200)",
        ),
    ),
    scene_aspectmode='cube',
    width=800,
    height=800,
)

fig.show()


In [15]:

OmegaD_M1 = OmegaQ2 - OmegaQ1
h = HamiltonianWithDrive3X3X(OmegaQ1, OmegaQ2, OmegaD_M1, PhiD, A)
print(h / (2 * np.pi))

[[  0.        +0.j  15.        +0.j   0.        +0.j]
 [ 15.        +0.j 400.        +0.j  21.21320344+0.j]
 [  0.        +0.j  21.21320344+0.j 400.        +0.j]]


In [17]:
a_m: complexfloating = 0
b_m: complexfloating = 1
c_m: complexfloating = 0
initialState_m: matrix = matrix([[a_m], [b_m], [c_m]])
OmegaD_M1 = OmegaQ2 - OmegaQ1
data: ndarray = np.array([[0, 0]])
stateData: ndarray = np.array([[0, 0, 0]])
τ: float = (np.pi / A) * np.sqrt(2)
precision: int = 10000
for t in tqdm(range(0, int(τ * precision)), desc="Computing ... ", colour="#12c462"):
    td = t / precision
    currentState: matrix = q.ComputeState(
        initialState_m, td, HamiltonianWithDrive3X3X(OmegaQ1, OmegaQ2, OmegaD_M1, PhiD, A))
    if t == 0:
        stateData[0] = np.array(currentState.T)
    else:
        stateData = np.r_[stateData, currentState.T]
    if t == 0:
        data[0] = np.array([td, q.ComputeStateProbability(currentState, 1)])
    else:
        data = np.r_[data, np.array(
            [[td, q.ComputeStateProbability(currentState, 1)]])]


Computing ... :   0%|          | 0/235 [00:00<?, ?it/s]C:\Users\seanw\AppData\Local\Temp\ipykernel_7428\2707526057.py:15: ComplexWarning:

Casting complex values to real discards the imaginary part

Computing ... : 100%|██████████| 235/235 [00:00<00:00, 9774.90it/s]


In [18]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=data[:, 0], y=data[:, 1], name="state 0 probability", mode='markers')
)
fig.update_yaxes(
    range=[-0.1, 1.1],
    dtick=0.5,
)
fig.update_layout(
    title={
        'text': "Rabi振荡：ωd=omegaq2 - omegaq1",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    xaxis_title="t(μs)",
    yaxis_title="1态概率",
    font=dict(
        color="black"
    ),
    width=800,
)
fig.show()
